# Word Embedding

### 1. 安装gensim库

In [3]:
! pip install gensim

Looking in indexes: http://repo.myhuaweicloud.com/repository/pypi/simple
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.0/24.0 MB 47.9 MB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 60.8/60.8 kB 19.9 MB/s eta 0:00:00

[notice] A new release of pip available: 22.1.2 -> 24.0
[notice] To update, run: pip install --upgrade pip


### 2. 同步数据至本地

In [1]:
import moxing as mox
mox.file.copy_parallel(src_url="s3://ascend-zyjs-dcyang/nlp/word_embedding/corpus.txt", dst_url='corpus.txt') 

INFO:root:Using MoXing-v2.0.1.rc0.ffd1c0c8-ffd1c0c8
INFO:root:Using OBS-Python-SDK-3.20.9.1
ERROR:root:Failed to call:
	func=<bound method ObsClient.getObjectMetadata of <moxing.framework.file.src.obs.client.ObsClient object at 0xffffac1d7a50>>
	args=('ascend-zyjs-dcyang', 'nlp/word_embedding/corpus.txt/')
	kwargs={}
ERROR:root:
	stat:429
	errorCode:None
	errorMessage:None
	reason:Too Many Requests
	request-id:
	retry:0


MoxFileRespException: ({'status': 429, 'reason': 'Too Many Requests', 'body': None, 'header': [('date', 'Tue, 19 Mar 2024 12:39:19 GMT'), ('connection', 'close'), ('x-reserved-indicator', '611'), ('error-code', 'TooManyRequests'), ('error-message', 'There is too many requests in a given amount of time.')], 'indicator': '611'}, 'Error occurs when accessing to OBS.\n\tPlease check the *stat* and *errorCode* above.\n\tYou can find some error solutions at: https://support.huaweicloud.com/sdk-python-devg-obs/obs_22_1502.html')

### 3. 导入依赖库

In [4]:
from multiprocessing import cpu_count
from gensim.models import Word2Vec
from gensim.models import KeyedVectors

### 4. 定义输入、输出文件路径

In [5]:
corpus_file = "corpus.txt"
out_embedding_file = "embedding.txt"

### 5. 查看函数文档

In [19]:
?Word2Vec

Init signature:
Word2Vec(
    sentences=None,
    corpus_file=None,
    vector_size=100,
    alpha=0.025,
    window=5,
    min_count=5,
    max_vocab_size=None,
    sample=0.001,
    seed=1,
    workers=3,
    min_alpha=0.0001,
    sg=0,
    hs=0,
    negative=5,
    ns_exponent=0.75,
    cbow_mean=1,
    hashfxn=<built-in function hash>,
    epochs=5,
    null_word=0,
    trim_rule=None,
    sorted_vocab=1,
    batch_words=10000,
    compute_loss=False,
    callbacks=(),
    comment=None,
    max_final_vocab=None,
    shrink_windows=True,
)
Docstring:     
Serialize/deserialize objects from disk, by equipping them with the `save()` / `load()` methods.

Warnings
--------
This uses pickle internally (among other techniques), so objects must not contain unpicklable attributes
such as lambda functions etc.
Init docstring:
Train, use and evaluate neural networks described in https://code.google.com/p/word2vec/.

Once you're finished training a model (=no more updates, only querying)
store

### 6. 词向量训练并保存

In [9]:
model = Word2Vec(corpus_file=corpus_file, vector_size=100, window=10, min_count=5, workers=cpu_count(), sg=0)
model.wv.save_word2vec_format(out_embedding_file, binary=False)

INFO:gensim.models.word2vec:collecting all words and their counts
INFO:gensim.models.word2vec:PROGRESS: at sentence #0, processed 0 words, keeping 0 word types
INFO:gensim.models.word2vec:collected 434258 word types from a corpus of 8163235 raw words and 6566 sentences
INFO:gensim.models.word2vec:Creating a fresh vocabulary
INFO:gensim.utils:Word2Vec lifecycle event {'msg': 'effective_min_count=5 retains 99249 unique words (22.85% of original 434258, drops 335009)', 'datetime': '2024-03-19T20:47:24.107229', 'gensim': '4.2.0', 'python': '3.7.10 | packaged by conda-forge | (default, Oct 13 2021, 22:05:51) \n[GCC 9.4.0]', 'platform': 'Linux-4.19.36-vhulk1907.1.0.h619.eulerosv2r8.aarch64-aarch64-with-centos-2.0-SP8', 'event': 'prepare_vocab'}
INFO:gensim.utils:Word2Vec lifecycle event {'msg': 'effective_min_count=5 leaves 7661631 word corpus (93.86% of original 8163235, drops 501604)', 'datetime': '2024-03-19T20:47:24.108794', 'gensim': '4.2.0', 'python': '3.7.10 | packaged by conda-forge 

In [21]:
!ls

corpus.txt  embedding.txt  word2vec.ipynb


### 7. 加载离线词向量

In [10]:
word2vec_model = KeyedVectors.load_word2vec_format("embedding.txt")

INFO:gensim.models.keyedvectors:loading projection weights from embedding.txt
INFO:gensim.utils:KeyedVectors lifecycle event {'msg': 'loaded (99249, 100) matrix of type float32 from embedding.txt', 'binary': False, 'encoding': 'utf8', 'datetime': '2024-03-19T20:49:51.330636', 'gensim': '4.2.0', 'python': '3.7.10 | packaged by conda-forge | (default, Oct 13 2021, 22:05:51) \n[GCC 9.4.0]', 'platform': 'Linux-4.19.36-vhulk1907.1.0.h619.eulerosv2r8.aarch64-aarch64-with-centos-2.0-SP8', 'event': 'load_word2vec_format'}


获取单个词的词向量

In [23]:
word2vec_model['中国']

array([ 0.27139708,  0.72190255, -0.08625011, -0.23090139, -0.33774328,
        0.09228144,  0.20106436,  0.5825225 ,  0.70327616, -0.40273708,
        0.21356277, -0.9992789 , -0.32095507, -0.25072524, -0.26337552,
        0.1876771 ,  0.5827109 , -0.4786952 ,  0.24628162, -0.3237592 ,
        0.7253267 ,  0.29445872,  0.1271547 , -0.02306593, -0.23750241,
        0.03963919,  0.09658901,  0.40956575,  0.01953161, -0.45225903,
        0.7912037 , -0.0720275 ,  0.11410014, -0.5900452 , -0.08244269,
        0.5009098 ,  0.71247345,  0.38276243,  0.01544921,  0.33081657,
       -0.3642058 , -0.02278505, -0.0363497 , -0.08772611,  0.40449047,
        0.12895723, -0.00583071,  0.23436488, -0.2452728 , -0.07917353,
       -0.3773923 ,  0.52499   ,  0.22502647, -0.31352532,  0.04571384,
       -0.05032074,  0.5059855 ,  0.10608203,  0.17131886,  0.32746804,
       -0.108876  , -0.29672408,  0.25252816,  0.10313778,  0.46843278,
        0.28052035, -0.18710832, -0.10961446,  0.30702814,  0.08

### 8. 相似度测试

In [11]:
testwords = ['金融', '喜欢', "中国", "北京"]
for word in testwords:
    res = word2vec_model.most_similar(word)
    print (word)
    print (res)

金融
[('国际贸易', 0.8395482301712036), ('保险', 0.812687337398529), ('金融业', 0.8124274015426636), ('服务业', 0.811759889125824), ('房地产', 0.8038193583488464), ('保险公司', 0.7991761565208435), ('金融服务', 0.7909917831420898), ('产业', 0.7815978527069092), ('银行', 0.7747089266777039), ('进出口', 0.7660459280014038)]
喜欢
[('讨厌', 0.7509140372276306), ('喜爱', 0.728961706161499), ('觉得', 0.710053026676178), ('漂亮', 0.704901397228241), ('喝酒', 0.6909952163696289), ('有点', 0.6817834377288818), ('样子', 0.6800354719161987), ('舒服', 0.6796457171440125), ('迷人', 0.6792800426483154), ('默默无闻', 0.6791799068450928)]
中国
[('东亚', 0.5217082500457764), ('北京', 0.5011240839958191), ('半殖民地', 0.48110827803611755), ('中华人民共和国', 0.47714969515800476), ('各省市', 0.47470974922180176), ('我国', 0.4700671136379242), ('内地', 0.46932893991470337), ('亚洲', 0.4631061851978302), ('大陆', 0.45580771565437317), ('中国政府', 0.4537569284439087)]
北京
[('上海', 0.73304283618927), ('南京', 0.6660677194595337), ('天津', 0.6637753844261169), ('广州', 0.6011340618133545), ('武汉', 0.579

### 9. 词向量文件回传obs

In [ ]:
mox.file.copy_parallel(src_url="embedding.txt", dst_url='s3://ascend-zyjs-dcyang/nlp/word_embedding/embedding.txt') 

### 10. 相似度测试plus

In [17]:
! pip install jieba

Looking in indexes: http://repo.myhuaweicloud.com/repository/pypi/simple
ERROR: Could not find a version that satisfies the requirement collections (from versions: none)
ERROR: No matching distribution found for collections


In [19]:
from collections import Counter
import jieba
# 初始化一个 Counter 对象来存储词频
word_freq = Counter()

# 读取文件并分词
with open(corpus_file, 'r', encoding='utf-8') as file:
    for line in file:
        # 对于中文文本，使用 jieba 进行分词
        words = list(jieba.cut(line.strip()))
        word_freq.update(words)
#print(word_freq)




Counter({' ': 8156711, '的': 367673, '在': 101239, '是': 74058, '年': 61985, '为': 60708, '和': 57972, '了': 49070, '与': 42044, '有': 38781, '中': 30225, '也': 29322, '被': 28268, '他': 27403, '等': 26206, '中国': 25793, '于': 24958, '后': 23453, '并': 23346, '而': 22118, '以': 20297, '人': 19850, '上': 19064, '之': 18228, '但': 18108, '美国': 17096, '不': 16738, '及': 15150, '其': 14816, '由': 14720, '对': 14648, '日': 14429, '将': 14185, '到': 14121, '都': 14084, '一个': 13614, '时': 12401, '台湾': 12140, '日本': 12014, '月': 11952, '国家': 11458, '或': 10981, '开始': 10615, '则': 10392, '这': 9998, '会': 9943, '香港': 9822, '包括': 9792, '至': 9763, '成为': 9575, '主要': 9394, '可以': 9331, '又': 9308, '使用': 9243, '世纪': 9168, '大': 9086, '个': 8971, '从': 8921, '就': 8865, '其中': 8791, '所': 8465, '没有': 8118, '大学': 7783, '历史': 7602, '称为': 7573, '地区': 7567, '认为': 7545, '最': 7517, '发展': 7511, '下': 7493, '人口': 7342, '由于': 7277, '以及': 7270, '新': 7266, '英国': 7155, '文化': 7011, '其他': 6996, '说': 6923, '因此': 6810, '可': 6741, '世界': 6717, '多': 6661, '即': 6619, 

In [25]:
testwords = ['金融', '喜欢', "中国", "北京"]
# CDOW
'''
word2vec_model = KeyedVectors.load_word2vec_format("embedding.txt")
cnt_all=0
for word in testwords:
    print(f'词汇: {word}')
    try:
        # 获取最相似的词
        similar_words = word2vec_model.most_similar(word)
        print('最相似的词及其词频:')
        cnt=0
        
        for similar_word, _ in similar_words:
            freq = word_freq.get(similar_word, 0)
            print(f'{similar_word}: {word_freq[similar_word]}')
            cnt=cnt+freq
        print(f'!{word} average_word_freq： {cnt/len(similar_words)}')
        cnt_all=cnt_all+cnt/len(similar_words)
    except KeyError:
        print(f'词汇"{word}"不在词汇表中。')
    print('----------')
print(f'average:{cnt_all/len(testwords)}')
'''
# sg
model = Word2Vec(corpus_file=corpus_file, vector_size=100, window=5, min_count=5, workers=cpu_count(), sg=1)
model.wv.save_word2vec_format(out_embedding_file, binary=False)
word2vec_model = KeyedVectors.load_word2vec_format("embedding.txt")
cnt_all=0
for word in testwords:
    print(f'词汇: {word}')
    try:
        # 获取最相似的词
        similar_words = word2vec_model.most_similar(word)
        print('最相似的词及其词频:')
        cnt=0
        
        for similar_word, _ in similar_words:
            freq = word_freq.get(similar_word, 0)
            print(f'{similar_word}: {word_freq[similar_word]}')
            cnt=cnt+freq
        print(f'!{word} average_word_freq： {cnt/len(similar_words)}')
        cnt_all=cnt_all+cnt/len(similar_words)
    except KeyError:
        print(f'词汇"{word}"不在词汇表中。')
    print('----------')
print(f'average:{cnt_all/len(testwords)}')


词汇: 金融
最相似的词及其词频:
证券期货: 6
金融服务: 28
房地产: 92
信贷: 22
国际经贸: 5
金融保险: 7
金融市场: 24
银行学: 5
投资银行: 13
商业银行: 73
!金融 average_word_freq： 27.5
----------
词汇: 喜欢
最相似的词及其词频:
讨厌: 67
喝酒: 54
吓人: 5
迟钝: 9
很会: 8
单恋: 7
偏爱: 16
惬意: 5
卖弄: 5
没够: 5
!喜欢 average_word_freq： 18.1
----------
词汇: 中国
最相似的词及其词频:
大陆: 3162
榜上有名: 5
内地: 543
中华人民共和国: 2491
中国地图出版社: 7
顾诚: 6
网年: 5
世界史: 19
近现代史: 14
李泽厚: 8
!中国 average_word_freq： 626.0
----------
词汇: 北京
最相似的词及其词频:
天津: 1343
上海: 3949
南京: 2068
北京市: 789
杭州: 980
沈阳: 644
西安: 834
京郊: 5
北京城: 29
高华: 11
!北京 average_word_freq： 1065.2
----------
average:434.20000000000005
